<a href="https://colab.research.google.com/github/agedgouda/Coursera_Capstone/blob/master/Where_Should_I_Live_in_LA.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
# @hidden_cell
!pip -q install folium
!pip install geocoder
!pip install pydotplus

     |████████████████████████████████| 102kB 3.9MB/s 


In [0]:
# @hidden_cell
from __future__ import print_function
from bs4 import BeautifulSoup
import requests 
from geopy.geocoders import Nominatim 
import requests 
import numpy as np # library for vectorized computation
import pandas as pd # library to process data as dataframes
import folium
import geocoder
from sklearn.cluster import KMeans
import matplotlib as mpl
import matplotlib.pyplot as plt
import matplotlib.colors as colors
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn import metrics
import matplotlib.pyplot as plt
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
import re
import json
from branca.colormap import linear
import locale
locale.setlocale( locale.LC_ALL, '' )
%matplotlib inline 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# Foursquare Information
CLIENT_ID = 'S35AD1C005HPBW0YRHEYKQ5PPU1Y3JTJVYAUDAWG35SEJV30' # your Foursquare ID
CLIENT_SECRET = 'DXJSLAZ451MNKIIHPYSVMULFYUUCC05K1GZU14HDT3WJSWWM' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
BING_KEY ='AjrFKOWxRFQeqK059icDBF98qBrdOCOB13g5jZ_ffOLjEGNTpcRasBnXneVcCH_w'

# Where should I live in Los Angeles

## Introduction

It is a truth universally acknowledged that most conversations in 21st century America are about where best to live in one's current city. This project seeks to simplify the process by analyzing a range of data for a specific city to identify neighborhood characteristics to create neighborhoods of similar clusters as well as decision tree to help someone moving to a new house or apartment in the Los Angeles area. If this is successful, the system will be expanded into other cit


## Data

The system will be using:
1. Foursquare for local venue. We may add yelp's api to expand the data set, based on price and availability.
2. Restaurant health reports from lacity.org.
3. Average home value by zip code from http://www.laalmanac.com/economy/ec37b.php
4. Libraries and cultural locations in each zip code from data.lacity.org



In [0]:
# @hidden_cell
# Work from the backup so I don't have to regenerate the data every time this runs. The previous code is to demonstrate how the data was processed
url = 'https://raw.githubusercontent.com/agedgouda/Coursera_Capstone/master/la-data.csv'
la_data = pd.read_csv(url)
print(la_data.shape)
la_data

(264, 433)


Unnamed: 0  Zip Code                                          Community  \
0             0     90001   Los Angeles (South Los Angeles), Florence-Graham   
1             1     90002         Los Angeles (Southeast Los Angeles, Watts)   
2             2     90003  Los Angeles (South Los Angeles, Southeast Los ...   
3             3     90004  Los Angeles (Hancock Park, Rampart Village, Vi...   
4             4     90005  Los Angeles (Hancock Park, Koreatown, Wilshire...   
5             5     90006  Los Angeles (Byzantine-Latino Quarter, Harvard...   
6             6     90007  Los Angeles (Southeast Los Angeles, Univerity ...   
7             7     90008  Los Angeles (Baldwin Hills, Crenshaw, Leimert ...   
8             8     90011                Los Angeles (Southeast Los Angeles)   
9             9     90012  Los Angeles (Downtown Civic Center, Chinatown,...   
10           10     90013  Los Angeles (Downtown Central, Downtown Fashio...   
11           11     90014  Los Angeles (Downtown Historic Core, Arts Dist...   
12           12     90015  Los Angeles (Dowtown Fashion District, South P...   
13           13     90016                 Los Angeles (Mid-City, West Adams)   
14           14     90017  Los Angeles (Downtown Bunker Hill, City West, ...   
15           15     90018         Los Angeles (Jefferson Park, Leimert Park)   
16           16     90019  Los Angeles (Arlington Heights, Country Club P...   
17           17     90020  Los Angeles (Hancock Park, Western Wilton, Wil...   
18           18     90022                                   East Los Angeles   
19           19     90023  Los Angeles (Boyle Heights), Commerce,  East L...   
20           20     90024                             Los Angeles (Westwood)   
21           21     90025           Los Angeles (Sawtelle, West Los Angeles)   
22           22     90026               Los Angeles (Echo Park, Silver Lake)   
23           23     90027  Los Angeles (Griffith Park, Hollywood, Los Feliz)   
24           24     90028                            Los Angeles (Hollywood)   
25           25     90029                       Los Angeles (East Hollywood)   
26           26     90031   Los Angeles (Lincoln Heights, Montecito Heights)   
27           27     90032            Los Angeles (El Sereno, Monterey Hills)   
28           28     90033                        Los Angeles (Boyle Heights)   
29           29     90034                                Los Angeles (Palms)   
30           30     90035                         Los Angeles (West Fairfax)   
31           31     90036  Los Angeles (Fairfax, Melrose, Miracle Mile, P...   
32           32     90037                    Los Angeles (South Los Angeles)   
33           33     90038                            Los Angeles (Hollywood)   
34           34     90039  Los Angeles (Atwater Village, Elysian Valley, ...   
35           35     90040                                           Commerce   
36           36     90041                           Los Angeles (Eagle Rock)   
37           37     90042                        Los Angeles (Highland Park)   
38           38     90043  Los Angeles (Hyde Park, View Park, Windsor Hills)   
39           39     90044            Athens, Los Angeles (South Los Angeles)   
40           40     90045  Los Angeles (Los Angeles International Airport...   
41           41     90046          Los Angeles (Mt Olympus) / West Hollywood   
42           42     90047                    Los Angeles (South Los Angeles)   
43           43     90048        Los Angeles (Mid-City West), West Hollywood   
44           44     90049           Los Angeles (Bel Air Estates, Brentwood)   
45           45     90056                                     Ladera Heights   
46           46     90057                             Los Angeles (Westlake)   
47           47     90059  Los Angeles (Southeast Los Angeles, Watts), Wi...   
48           48     90061                    Los Angeles (South Los Angeles)   
49   

In [0]:
la_analyze = la_data
la_analyze['Historic Landmark'] = la_analyze[['Historic','artifacts','fossils','historic','historic landscape','tree - historic oak','tree grove','taxidermy - artifacts','white oil seep','Historic Site']].sum(axis='columns')
la_analyze['Doctors and Medicine'] = la_analyze[['Drugstore','Eye Doctor','Medical Center','Dentist\'s Office','Doctor\'s Office','Optical Shop']].sum(axis='columns')
la_analyze['Colleges and Universities'] = la_analyze[['Fraternity House','College Bookstore','College Cafeteria','College Residence Hall','College Theater','University','General College & University']].sum(axis='columns')
la_analyze['Culture'] = la_analyze[['museums','Art Museum','Museum','Art Gallery','Cultural Center','History Museum','Libraries']].sum(axis='columns')
la_analyze['Clothing Retail'] = la_analyze[['Boutique','Bridal Shop','Kids Store','Kitchen Supply Store','Leather Goods Store','Lingerie Store','Men\'s Store','Shoe Store','Women\'s Store','Tailor Shop','Thrift / Vintage Store']].sum(axis='columns')
la_analyze['Personal Grooming'] = la_analyze[['Salon / Barbershop','Nail Salon','Massage Studio','Spa']].sum(axis='columns')
la_analyze['Retail'] = la_analyze[['Accessories Store','Bike Shop','Board Shop','Bookstore','Clothing Store','Comic Shop','Convenience Store','Cosmetics Shop','Electronics Store','Fabric Shop','Flea Market','Flower Shop','Furniture / Home Store','Gift Shop','Hobby Shop','Hunting Supply','Liquor Store','Market','Miscellaneous Shop','Mobile Phone Shop','Mobility Store','Motorcycle Shop','Motorsports Shop','Music Store','Newsstand','Other Repair Shop','Pawn Shop','Pet Store','Pharmacy','Photography Lab','Photography Studio','Print Shop','Record Shop','Shipping Store','Shop & Service','Smoke Shop','Sporting Goods Shop','Stationery Store','Supplement Shop','Tanning Salon','Tattoo Parlor','Toy / Game Store','Video Game Store','Video Store','Arts & Crafts Store','Camera Store','prints','records','bookstore','Antique Shop']].sum(axis='columns')
la_analyze['Food and Beverage Retailer'] = la_analyze[['Fish Market','Butcher','Fruit & Vegetable Store','Gourmet Shop','Health Food Store','Organic Grocery','Wine Shop','Cheese Shop','Chocolate Shop','Beer Store','Candy Store','Farmers Market','Bakery']].sum(axis='columns')
la_analyze['Large Retail'] = la_analyze[['Big Box Store','Carpet Store','Department Store','Discount Store','Grocery Store','Hardware Store','Outdoor Supply Store','Outlet Mall','Paper / Office Supplies Store','Warehouse Store','Supermarket','Shopping Mall','Shopping Plaza']].sum(axis='columns')
la_analyze['Bars and Clubs'] = la_analyze[['Beer Bar','Beer Garden','Bar','Cocktail Bar','Dive Bar','Dive Spot','Gay Bar','Hookah Bar','Hotel Bar','Irish Pub','Jazz Club','Karaoke Bar','Lounge','Roof Deck','Sake Bar','Speakeasy','Sports Bar','Strip Club','Tiki Bar','Whisky Bar','Wine Bar','Pool Hall','Pub']].sum(axis='columns')
la_analyze['Movies and Theaters'] = la_analyze[['Comedy Club','Casino','Concert Hall','Indie Movie Theater','Indie Theater','Movie Theater','Multiplex','Opera House','Rock Club','Theater','Performing Arts Venue','Music Venue','Nightclub','Nightlife Spot']].sum(axis='columns')
la_analyze['Drinking'] = la_analyze[['Brewery','Distillery','Winery']].sum(axis='columns')
la_analyze['Parks'] = la_analyze[['State / Provincial Park','Garden','Playground','Park','Mountain','Nature Preserve','Other Great Outdoors','Plaza','Resort','Rest Area']].sum(axis='columns')
la_analyze['Professional Sports'] = la_analyze[['Football Stadium','Athletics & Sports','Baseball Stadium','Basketball Stadium','Hockey Arena','Soccer Stadium','Stadium']].sum(axis='columns')
la_analyze['Outdoor Athletics'] = la_analyze[['Baseball Field','Basketball Court','Campground','Dog Run','Golf Course','Pool','Recreation Center','Track','Trail','Volleyball Court','Boxing Gym','Skate Park','Soccer Field','Tennis Court','Surf Spot']].sum(axis='columns')
la_analyze['Indoor Athletics'] = la_analyze[['Bowling Alley','Gym','Gym / Fitness Center','Gym Pool','Gymnastics Gym','Skating Rink','Pilates Studio','Cycle Studio','Dance Studio','Martial Arts Dojo','Yoga Studio','Hotel Pool']].sum(axis='columns')
la_analyze['Restaurants'] = la_analyze[['American Restaurant','Afghan Restaurant','African Restaurant','Argentinian Restaurant','Asian Restaurant','Australian Restaurant','BBQ Joint','Bagel Shop','Bistro','Brazilian Restaurant','Breakfast Spot','Bubble Tea Shop','Buffet','Burger Joint','Burmese Restaurant','Burrito Place','Cantonese Restaurant','Caribbean Restaurant','Chinese Restaurant','Churrascaria','Coffee Shop','Comfort Food Restaurant','Creperie','Cuban Restaurant','Cupcake Shop','Dessert Shop','Dim Sum Restaurant','Diner','Donburi Restaurant','Doner Restaurant','Dongbei Restaurant','Donut Shop','Dumpling Restaurant','Eastern European Restaurant','Empanada Restaurant','English Restaurant','Falafel Restaurant','Fast Food Restaurant','Filipino Restaurant','Fish & Chips Shop','Food','Food & Drink Shop','Food Court','Food Service','Food Stand','Food Truck','French Restaurant','Fried Chicken Joint','Frozen Yogurt Shop','Gaming Cafe','Gastropub','German Restaurant','Greek Restaurant','Halal Restaurant','Hawaiian Restaurant','Hot Dog Joint','Hotpot Restaurant','Ice Cream Shop','Indian Restaurant','Indonesian Restaurant','Italian Restaurant','Japanese Curry Restaurant','Japanese Restaurant','Jewish Restaurant','Juice Bar','Kebab Restaurant','Korean Restaurant','Kosher Restaurant','Latin American Restaurant','Lebanese Restaurant','Mediterranean Restaurant','Mexican Restaurant','Middle Eastern Restaurant','Mongolian Restaurant','Moroccan Restaurant','New American Restaurant','Noodle House','Paella Restaurant','Pakistani Restaurant','Persian Restaurant','Peruvian Restaurant','Pie Shop','Pizza Place','Poke Place','Ramen Restaurant','Restaurant','Salad Place','Salvadoran Restaurant','Sandwich Place','Scandinavian Restaurant','Seafood Restaurant','Shabu-Shabu Restaurant','Smoothie Shop','Snack Place','Soup Place','South American Restaurant','South Indian Restaurant','Southern / Soul Food Restaurant','Spanish Restaurant','Wings Joint','Steakhouse','Street Food Gathering','Sushi Restaurant','Szechuan Restaurant','Taco Place','Taiwanese Restaurant','Tapas Restaurant','Tea Room','Tex-Mex Restaurant','Thai Restaurant','Truck Stop','Udon Restaurant','Vegetarian / Vegan Restaurant','Vietnamese Restaurant','Cafeteria','Café','Cajun / Creole Restaurant']].sum(axis='columns')
la_analyze['Video Games'] = la_analyze[['Arcade','Gaming Cafe']].sum(axis='columns')
la_analyze['Travel Amenities'] = la_analyze[['Bed & Breakfast','Hostel','Hotel','Motel','Taxi Stand','Travel Lounge','Vacation Rental','Rental Car Location']].sum(axis='columns')
la_analyze['Travel'] = la_analyze[['Airport Terminal','Boat or Ferry','Bus Station','Bus Stop','Light Rail Station','Train Station']].sum(axis='columns')
la_analyze['Cars'] = la_analyze[['Auto Dealership','Auto Garage','Auto Workshop','Automotive Shop','Car Wash','Gas Station']].sum(axis='columns')
la_analyze['Water'] = la_analyze[['Harbor / Marina','Lake','Pier','Beach']].sum(axis='columns')
la_analyze['Public Art'] = la_analyze[['sculpture','sculpture - concrete','sculpture - fence','sculpture - fountain','sculpture - metal','sculpture - wood','mural','mural - painted','mural - tile','painting - architectural watercolor','character defining feature - urban open space','Civic Art','Mural - mosaic','Fountain','Pedestrian Plaza','Scenic Lookout']].sum(axis='columns')


In [0]:
la_analyze_testnormalized=la_analyze[['Marijuana Dispenseries','Post Office','Theme Park','ATM','Animal Shelter','Historic Landmark','Doctors and Medicine','Colleges and Universities','Culture','Clothing Retail','Personal Grooming','Retail','Food and Beverage Retailer','Large Retail','Bars and Clubs','Movies and Theaters','Drinking','Parks','Professional Sports','Outdoor Athletics','Indoor Athletics','Restaurants','Video Games','Travel Amenities','Travel','Cars','Water']]
la_analyze_testnormalized =la_analyze_testnormalized/la_analyze_testnormalized.max()
la_analyze_testnormalized.dropna(axis='columns',inplace=True)
la_analyze_testnormalized.head()

Marijuana Dispenseries  Post Office  Theme Park  ATM  Animal Shelter  \
0                1.000000          0.0         0.0  0.0             0.0   
1                0.047619          0.0         0.0  0.0             0.0   
2                0.309524          0.0         0.0  0.0             0.0   
3                0.166667          0.0         0.0  0.0             0.0   
4                0.380952          0.0         0.0  0.0             0.0   

   Historic Landmark  Doctors and Medicine  Colleges and Universities  \
0            0.00000                   0.0                        0.0   
1            0.02381                   0.0                        0.0   
2            0.00000                   0.0                        0.0   
3            0.00000                   0.0                        0.0   
4            0.00000                   0.0                        0.0   

    Culture  Clothing Retail  Personal Grooming    Retail  \
0  0.000000         0.000000           0.000000  0.129032   
1  0.263158         0.076923           0.000000  0.096774   
2  0.000000         0.000000           0.000000  0.096774   
3  0.000000         0.000000           0.142857  0.354839   
4  0.000000         0.000000           0.428571  0.419355   

   Food and Beverage Retailer  Large Retail  Bars and Clubs  \
0                    0.142857      0.272727             0.0   
1                    0.000000      0.090909             0.0   
2                    0.000000      0.090909             0.0   
3                    0.285714      0.090909             0.1   
4                    0.428571      0.090909             0.4   

   Movies and Theaters  Drinking  Parks  Professional Sports  \
0             0.000000       0.0    0.0                  0.0   
1             0.000000       0.0    0.2                  0.0   
2             0.000000       0.0    0.0                  0.0   
3             0.066667       0.0    0.2                  0.0   
4             0.000000       0.0    0.2                  0.0   

   Outdoor Athletics  Indoor Athletics  Restaurants  Video Games  \
0              0.000          0.000000     0.178082          0.0   
1              0.000          0.000000     0.068493          0.0   
2              0.000          0.000000     0.109589          0.0   
3              0.000          0.000000     0.287671          0.0   
4              0.125          0.090909     0.986301          0.0   

   Travel Amenities  Travel  Cars  Water  
0               0.0   0.000   0.0    0.0  
1               0.0   0.125   0.0    0.0  
2               0.0   0.000   0.0    0.0  
3               0.1   0.000   0.0    0.0  
4               0.2   0.000   0.0    0.0

In [0]:
la_analyze_testnormalized[['Zip Code','Community','2018 Cost','2018 Cost Growth','2017 Cost Growth','2016 Cost Growth','Lat','Long']] = la_data[['Zip Code','Community','2018 Cost','2018 Cost Growth','2017 Cost Growth','2016 Cost Growth','Lat','Long']]
la_analyze_testnormalized.head()

Marijuana Dispenseries  Post Office  Theme Park  ATM  Animal Shelter  \
0                1.000000          0.0         0.0  0.0             0.0   
1                0.047619          0.0         0.0  0.0             0.0   
2                0.309524          0.0         0.0  0.0             0.0   
3                0.166667          0.0         0.0  0.0             0.0   
4                0.380952          0.0         0.0  0.0             0.0   

   Historic Landmark  Doctors and Medicine  Colleges and Universities  \
0            0.00000                   0.0                        0.0   
1            0.02381                   0.0                        0.0   
2            0.00000                   0.0                        0.0   
3            0.00000                   0.0                        0.0   
4            0.00000                   0.0                        0.0   

    Culture  Clothing Retail  Personal Grooming    Retail  \
0  0.000000         0.000000           0.000000  0.129032   
1  0.263158         0.076923           0.000000  0.096774   
2  0.000000         0.000000           0.000000  0.096774   
3  0.000000         0.000000           0.142857  0.354839   
4  0.000000         0.000000           0.428571  0.419355   

   Food and Beverage Retailer  Large Retail  Bars and Clubs  \
0                    0.142857      0.272727             0.0   
1                    0.000000      0.090909             0.0   
2                    0.000000      0.090909             0.0   
3                    0.285714      0.090909             0.1   
4                    0.428571      0.090909             0.4   

   Movies and Theaters  Drinking  Parks  Professional Sports  \
0             0.000000       0.0    0.0                  0.0   
1             0.000000       0.0    0.2                  0.0   
2             0.000000       0.0    0.0                  0.0   
3             0.066667       0.0    0.2                  0.0   
4             0.000000       0.0    0.2                  0.0   

   Outdoor Athletics  Indoor Athletics  Restaurants  Video Games  \
0              0.000          0.000000     0.178082          0.0   
1              0.000          0.000000     0.068493          0.0   
2              0.000          0.000000     0.109589          0.0   
3              0.000          0.000000     0.287671          0.0   
4              0.125          0.090909     0.986301          0.0   

   Travel Amenities  Travel  Cars  Water  Zip Code  \
0               0.0   0.000   0.0    0.0     90001   
1               0.0   0.125   0.0    0.0     90002   
2               0.0   0.000   0.0    0.0     90003   
3               0.1   0.000   0.0    0.0     90004   
4               0.2   0.000   0.0    0.0     90005   

                                           Community  2018 Cost  \
0   Los Angeles (South Los Angeles), Florence-Graham   369300.0   
1         Los Angeles (Southeast Los Angeles, Watts)   372600.0   
2  Los Angeles (South Los Angeles, Southeast Los ...   379800.0   
3  Los Angeles (Hancock Park, Rampart Village, Vi...  1590400.0   
4  Los Angeles (Hancock Park, Koreatown, Wilshire...  1721400.0   

   2018 Cost Growth  2017 Cost Growth  2016 Cost Growth       Lat       Long  
0          0.057863          0.092303          0.154624  33.97880 -118.24980  
1          0.067928          0.132792          0.106719  33.94870 -118.24342  
2          0.087629          0.090909          0.159783  33.96288 -118.27207  
3          0.044666          0.013987          0.130402  34.07538 -118.29992  
4          0.195749          0.008123          0.072314  34.05984 -118.29373

In [0]:
low = la_analyze_testnormalized['2018 Cost'].quantile(0.25)
medium = la_analyze_testnormalized['2018 Cost'].quantile(0.5)
high = la_analyze_testnormalized['2018 Cost'].quantile(0.75)
print (low, medium, high)

550175.0 683350.0 1008750.0


In [0]:
def f(Cost,AnimalShelter,ATM,BarsandClubs,Cars,ClothingRetail,CollegesandUniversities,Culture,DoctorsandMedicine,Drinking,FoodandBeverageRetailer,HistoricLandmark,IndoorAthletics,LargeRetail,MarijuanaDispenseries,MoviesandTheaters,OutdoorAthletics,Parks,PersonalGrooming,PostOffice,ProfessionalSports,Restaurants,Retail,Travel,TravelAmenities,VideoGames,Water):
    return Cost,AnimalShelter,ATM,BarsandClubs,Cars,ClothingRetail,CollegesandUniversities,Culture,DoctorsandMedicine,Drinking,FoodandBeverageRetailer,HistoricLandmark,IndoorAthletics,LargeRetail,MarijuanaDispenseries,MoviesandTheaters,OutdoorAthletics,Parks,PersonalGrooming,PostOffice,ProfessionalSports,Restaurants,Retail,Travel,TravelAmenities,VideoGames,Water


In [240]:
recommendationChooser = interactive(f
,Cost=widgets.Dropdown(options=[('Under 500k', 0), ('500k-700k', 1), ('700k-900k', 2), ('Over 900k', 3)], value=1,description = 'Cost',disabled=False)
,AnimalShelter=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Animal Shelter')
,ATM=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'ATM')
,BarsandClubs=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Bars and Clubs')
,Cars=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Cars')
,ClothingRetail=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Clothing Retail')
,CollegesandUniversities=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Colleges and Universities')
,Culture=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Culture')
,DoctorsandMedicine=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Doctors and Medicine')
,Drinking=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Drinking')
,FoodandBeverageRetailer=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Food and Beverage Retailer')
,HistoricLandmark=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Historic Landmark')
,IndoorAthletics=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Indoor Athletics')
,LargeRetail=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Large Retail')
,MarijuanaDispenseries=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Marijuana Dispenseries')
,MoviesandTheaters=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Movies and Theaters')
,OutdoorAthletics=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Outdoor Athletics')
,Parks=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Parks')
,PersonalGrooming=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Personal Grooming')
,PostOffice=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Post Office')
,ProfessionalSports=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Professional Sports')
,Restaurants=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Restaurants')
,Retail=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Retail')
,Travel=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Travel')
,TravelAmenities=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Travel Amenities')
,VideoGames=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Video Games')
,Water=widgets.IntSlider(min=0, max=10, step=1, value=0,description = 'Water')
);

recommendationChooser


interactive(children=(Dropdown(description='Cost', index=1, options=(('Under 500k', 0), ('500k-700k', 1), ('70…

In [249]:
cols=['2018 Cost','Animal Shelter','ATM','Bars and Clubs','Cars','Clothing Retail','Colleges and Universities','Culture','Doctors and Medicine','Drinking','Food and Beverage Retailer','Historic Landmark','Indoor Athletics','Large Retail','Marijuana Dispenseries','Movies and Theaters','Outdoor Athletics','Parks','Personal Grooming','Post Office','Professional Sports','Restaurants','Retail','Travel','Travel Amenities','Video Games','Water']
query = pd.DataFrame([recommendationChooser.result],columns=cols)

if recommendationChooser.result[0] == 0:
    la_filtered = la_analyze_testnormalized.loc[la_analyze_testnormalized['2018 Cost'] <= 500000.0]
elif recommendationChooser.result[0] == 1:
    la_filtered = la_analyze_testnormalized.loc[(la_analyze_testnormalized['2018 Cost'] >= 500000.0) & (la_analyze_testnormalized['2018 Cost'] <= 700000.0)]
elif recommendationChooser.result[0] == 2:
    la_filtered = la_analyze_testnormalized.loc[(la_analyze_testnormalized['2018 Cost'] >= 700000.0) & (la_analyze_testnormalized['2018 Cost'] <= 900000.0)]
elif recommendationChooser.result[0] == 3:
    la_filtered = la_analyze_testnormalized.loc[la_analyze_testnormalized['2018 Cost'] > 900000.0]
filters = recommendationChooser.result[1:len(recommendationChooser.result)]

cols=['Animal Shelter','ATM','Bars and Clubs','Cars','Clothing Retail','Colleges and Universities','Culture','Doctors and Medicine','Drinking','Food and Beverage Retailer','Historic Landmark','Indoor Athletics','Large Retail','Marijuana Dispenseries','Movies and Theaters','Outdoor Athletics','Parks','Personal Grooming','Post Office','Professional Sports','Restaurants','Retail','Travel','Travel Amenities','Video Games','Water']
recommendationTable = ((la_filtered[cols]*filters).sum(axis=1)/query[cols].sum(axis=1)[0])

scleem = recommendationTable.reset_index()
la_filtered.reset_index(inplace=True)

scleem.rename(columns={0:"Score"},inplace=True)
#scleem['Score'] = scleem['Score']/scleem['Score'].max()
#scleem.drop(['index'],axis=1,inplace = True)
la_recommend = la_filtered.drop(['index'],axis=1)
la_recommend['Score'] = scleem['Score']
la_recommend_final = la_recommend.loc[la_recommend['Score'] > 0].copy()
la_recommend_final['Score'] = la_recommend['Score']/la_recommend['Score'].max()
#la_recommend_final = 
la_recommend_final.sort_values(by=['Score'],ascending=False,inplace=True)
la_recommend_final.head()



Marijuana Dispenseries  Post Office  Theme Park  ATM  Animal Shelter  \
38                0.238095          0.0         0.0  0.0             0.0   
8                 0.238095          0.0         0.0  0.0             0.0   
12                0.333333          0.0         0.0  0.0             0.0   
2                 0.357143          0.0         0.0  0.0             0.0   
27                0.380952          0.0         0.0  0.0             0.0   

    Historic Landmark  Doctors and Medicine  Colleges and Universities  \
38            0.00000                   0.0                        1.0   
8             0.02381                   0.0                        0.0   
12            0.00000                   0.0                        0.0   
2             0.00000                   0.0                        0.0   
27            0.00000                   0.0                        0.0   

     Culture  Clothing Retail  Personal Grooming    Retail  \
38  0.421053         0.076923           0.285714  0.451613   
8   0.052632         0.153846           0.000000  0.096774   
12  0.105263         0.000000           0.000000  0.290323   
2   0.052632         0.076923           0.142857  0.419355   
27  0.052632         0.000000           0.142857  0.161290   

    Food and Beverage Retailer  Large Retail  Bars and Clubs  \
38                    0.714286      0.000000             0.1   
8                     0.285714      0.000000             0.2   
12                    0.142857      0.181818             0.1   
2                     0.285714      0.090909             0.8   
27                    0.285714      0.272727             0.1   

    Movies and Theaters  Drinking  Parks  Professional Sports  \
38             0.066667       0.0    0.4                  0.1   
8              0.000000       1.0    0.0                  0.1   
12             0.000000       0.0    0.2                  0.0   
2              0.466667       0.5    0.2                  0.0   
27             0.000000       0.0    0.0                  0.0   

    Outdoor Athletics  Indoor Athletics  Restaurants  Video Games  \
38               0.00          0.090909     0.561644          0.0   
8                0.25          0.181818     0.410959          0.0   
12               0.00          0.181818     0.410959          0.0   
2                0.00          0.545455     0.643836          0.0   
27               0.00          0.000000     0.232877          0.0   

    Travel Amenities  Travel      Cars  Water  Zip Code  \
38               0.0     0.0  0.000000    0.0     91711   
8                0.0     0.0  0.666667    0.0     90501   
12               0.2     0.0  0.666667    0.0     90717   
2                0.4     0.0  0.000000    0.0     90014   
27               0.1     0.0  0.666667    0.0     91316   

                                            Community  2018 Cost  \
38                                          Claremont   704200.0   
8              Torrance, Los Angeles (Harbor Gateway)   740800.0   
12                                             Lomita   711700.0   
2   Los Angeles (Downtown Historic Core, Arts Dist...   723500.0   
27                               Los Angeles (Encino)   871400.0   

    2018 Cost Growth  2017 Cost Growth  2016 Cost Growth       Lat       Long  \
38          0.018808          0.047590          0.045808  34.10054 -117.71762   
8           0.065286          0.061355          0.060709  33.83281 -118.32161   
12          0.046002          0.057507          0.068593  33.79116 -118.31465   
2           0.053283          0.036830          0.017665  34.04220 -118.25271   
27          0.050892          0.041970          0.108357  34.16685 -118.52034   

       Score  
38  1.000000  
8   0.554537  
12  0.524025  
2   0.512427  
27  0.492393

In [250]:
query_clean = query.loc[:, (query != 0).any(axis=0)]
query_clean

2018 Cost  Bars and Clubs  Cars  Colleges and Universities  Culture  \
0          2               7     7                          8        7   

   Historic Landmark  
0                  1

In [0]:
#url = 'https://raw.githubusercontent.com/agedgouda/Coursera_Capstone/master/ZIP%20Codes.geojson'


import urllib.request

with urllib.request.urlopen("https://raw.githubusercontent.com/agedgouda/Coursera_Capstone/master/ZIP%20Codes.geojson") as url:
    la_zip_boundries = json.loads(url.read().decode())



colormap = linear.YlOrRd_09.scale(
    la_recommend_final.Score.min(),
    la_recommend_final.Score.max())
colormap.caption = 'Preference Match'

score_dict = la_recommend.set_index('Zip Code')['Score']

def get_color(feature):
    value = score_dict.get(float(feature['properties']['name']))
    if value is None or value == 0.0:
        return '' # MISSING -> gray
    else:
        return colormap(value)

def get_dot_color(zip):
    value = score_dict.get(zip)
    if value is None or value == 0.0:
        return '' # MISSING -> gray
    else:
        return colormap(value)


In [0]:
from IPython.core.display import display, HTML

address = 'Los Angeles, CA'
geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

with urllib.request.urlopen("http://s3-us-west-2.amazonaws.com/boundaries.latimes.com/archive/1.0/boundary-set/zip-code-tabulation-areas-2012.geojson") as url:
    tmp = json.loads(url.read().decode())

bob = []
for i in range(len(tmp['features'])):
  if len(la_recommend_final[la_recommend_final['Zip Code'].astype(str).str.match(tmp['features'][i]['properties']['name'])]):
    bob.append(tmp['features'][i])

new_json = dict.fromkeys(['type','features'])
new_json['type'] = 'FeatureCollection'
new_json['features'] = bob

map_la = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, cost, neighborhood,score in zip(la_recommend_final['Lat'], la_recommend_final['Long'], la_recommend_final['2018 Cost'], la_recommend_final['Community'], la_recommend_final['Score']):
    if score <=0:
        break
    label = '{}, {}'.format(neighborhood, locale.currency( cost, grouping=True ))
    label = folium.Popup(label, parse_html=True)
    folium.GeoJson(
      new_json,
      style_function=lambda feature: {
          'fillColor': get_color(feature),
          'color': 'black',
          'weight': .1,
          'fillOpacity': 0.05,
      }
    ).add_to(map_la)

    folium.Marker(
        [lat, lng],
        #radius=5,
        popup=label,
        #color='#000080',
        #fill=True,
        #fill_color='white',
        #fill_opacity=0.2,
        #parse_html=False
    ).add_to(map_la) 

colormap.add_to(map_la)
map_la.save('/content/gdrive/My Drive/Colab Notebooks/preferences.html')










In [0]:
from google.colab import drive
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
len(la_zip_boundries)


11

In [0]:
from IPython.core.display import display, HTML

address = 'Los Angeles, CA'
geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

bob = []
for i in range(len(tmp['features'])):
  if len(la_recommend_final[la_recommend_final['Zip Code'].astype(str).str.match(tmp['features'][i]['properties']['name'])]):
    bob.append(tmp['features'][i])

new_json = dict.fromkeys(['type','features'])
new_json['type'] = 'FeatureCollection'
new_json['features'] = bob


map_los_angeles = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, cost, neighborhood,score,zip_code in zip(la_recommend_final['Lat'], la_recommend_final['Long'], la_recommend_final['2018 Cost'], la_recommend_final['Community'], la_recommend_final['Score'], la_recommend_final['Zip Code']):
    if score <=0:
        break
    label = '{}, {}'.format(neighborhood, locale.currency( cost, grouping=True ))
    label = folium.Popup(label, parse_html=True)

    folium.GeoJson(
      new_json,
      name='geojson',
      style_function=lambda feature: {
          'fillColor': get_color(feature),
          'color': 'black',
          'weight': .3,
          'fillOpacity': 0.7,
      }
    ).add_to(map_los_angeles)

    folium.CircleMarker(
        [lat, lng],
        radius=10,
        popup=label,
        color=get_dot_color(zip_code),
        weight=.3,
        fill=True,
        fill_color=get_dot_color(zip_code),
        fill_opacity=0.7,
        parse_html=False
    ).add_to(map_los_angeles) 

colormap.add_to(map_los_angeles)


map_los_angeles.save('/content/gdrive/My Drive/Colab Notebooks/new.html')

In [0]:
with urllib.request.urlopen("https://raw.githubusercontent.com/agedgouda/Coursera_Capstone/master/ZIP%20Codes.geojson") as url:
    la_zip_test = json.loads(url.read().decode())

In [0]:
with urllib.request.urlopen("http://s3-us-west-2.amazonaws.com/boundaries.latimes.com/archive/1.0/boundary-set/zip-code-tabulation-areas-2012.geojson") as url:
    tmp = json.loads(url.read().decode())

bob = []
for i in range(len(tmp['features'])):
  if len(la_recommend_final[la_recommend_final['Zip Code'].astype(str).str.match(tmp['features'][i]['properties']['name'])]):
    bob.append(tmp['features'][i])

new_json = dict.fromkeys(['type','features'])
new_json['type'] = 'FeatureCollection'
new_json['features'] = bob

In [0]:
len(bob)

24